In [53]:
# 기본
import requests
from bs4 import BeautifulSoup
import re
import time
from io import BytesIO
import pandas as pd
import datetime
import json
import glob
import os

#  기초정보
# 0은 월요일, 1은 화요일, 2는 수요일, 3은 목요일, 4는 금요일 ,5는 토요일 ,6은 일요일
weekday_str = datetime.datetime.now().weekday() # 주 :일자로 변환
if weekday_str == 6 :
    dt_time = datetime.datetime.now() - datetime.timedelta(days=2)
elif weekday_str == 5 :
    dt_time = datetime.datetime.now() - datetime.timedelta(days=1)
else:
    dt_time = datetime.datetime.now()

dt_str = datetime.datetime.strftime(dt_time, '%Y%m%d')
print('작업일자 ==> ', dt_str)

작업일자 ==>  20220325


In [54]:
# 폴더

folder_nm = '주식_' + dt_str
path = './' + folder_nm
if os.path.isdir(path) == False : os.mkdir(folder_nm) 

In [56]:
global siljuk_lists
siljuk_lists = []
file_siljuk_nm = '실적_'+dt_str+'.csv'

def siljuk_def(code, code_nm):

    url = 'https://finance.naver.com/item/main.naver?code={}'.format(code)
    headers = {"User-Agent":"Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/99.0.4844.74 Safari/537.36"}
    res = requests.get(url, headers=headers)
    res.raise_for_status()
    soup = BeautifulSoup(res.text, 'lxml')

    # 종목코드, 명
    # ---------------------------------------------------------------------
#     code = '098120'
#     code_nm = '마이크로컨텍솔'

#     siljuk_lists.append(['---------------------------------------------------------------------'])
#     siljuk_lists.append([code, code_nm])
#     siljuk_lists.append(['---------------------------------------------------------------------'])

#     # 시가총액
#     # ---------------------------------------------------------------------
#     sum_amt_list =[code, code_nm, '시가총액']
#     sum_amt = soup.find('div', attrs={'class':'first'}).find('td').get_text().split()[0]\
#              + ' (' + soup.find('div', attrs={'class':'first'}).find('td').get_text().split()[1]\
#              + ')'

#     sum_amt_list.append(sum_amt)
#     siljuk_lists.append(sum_amt_list)

#     # 투자의견
#     # ---------------------------------------------------------------------
#     # PER/EPS 정보
#     # ---------------------------------------------------------------------
#     sum_per_list = [code, code_nm,'PER/EPS 정보']
#     try :
#         sum_per = soup.find('table', attrs={'class':'per_table'}).find('em', attrs={'id':'_per'}).get_text()+' (배)'
#     except:
#         sum_per = 'N/A'
        
    
#     sum_per_list.append(sum_per)
#     siljuk_lists.append(sum_per_list)

#     동종업종 PER
#     ---------------------------------------------------------------------
#     ---------------------------------------------------------------------
#     ---------------------------------------------------------------------


    # title
    # ---------------------------------------------------------------------
    try:
        titles = soup.find_all('div', attrs={'class':'sub_section'})[4].find('thead').find_all('tr')[1].find_all('th')
    except:
        return
    
    sub_title = []
    sub_title.append('종목코드')
    sub_title.append('종목한글명')
    sub_title.append('주요재무정보')
    for title in titles:
        sub_title.append(title.get_text().strip())

        # 재무정보 실적
    # ---------------------------------------------------------------------
    siljuk_lists.append(sub_title)
    siljuks = soup.find_all('div', attrs={'class':'sub_section'})[4].find('tbody').find_all('tr')
    for idx, siljuk in enumerate(siljuks):
        title = siljuk.find('th').get_text()
        title_values = []
        title_values.append(code)
        title_values.append(code_nm)
        title_values.append(title)
        sub_siljuk = siljuk.find_all('td')
        for a_value in sub_siljuk:
            sub_value = a_value.get_text().strip()
            title_values.append(sub_value)

        siljuk_lists.append(title_values)

    # ---------------------------------------------------------------------

    #siljuk_lists.append(['---------------------------------------------------------------------'])


# 전종목기본정보_20220320.xlsx
file_nm_1 = '전종목기본정보_'+dt_str+'.xlsx'
df1 = pd.read_excel(folder_nm+'/'+ file_nm_1, index_col= 0, dtype={'단축코드':str})
# 칼럼변경 (단축코드->종목코드)
df1.rename(columns={"단축코드":"종목코드"}, inplace=True)
# 칼럼삭제 (표준코드)
df1.drop(['표준코드','한글 종목명','영문 종목명','상장일'], axis='columns', inplace=True) # 칼럼단위 삭제
# for column_name, item in df1.iteritems():
for index, row in df1.iterrows():
    code = row[0]
    code_nm = row[1]
    print(index, row[0] , row[1])
    siljuk_def(code, code_nm)
    
print('siljuk sub complete')    
# for siljuk_list in siljuk_lists:
#     print(siljuk_list)
    
with open(folder_nm+'/'+ file_siljuk_nm,'w', encoding='utf-8') as f:
    for siljuk_list in siljuk_lists:
        data_l = ''
        for idx, data in enumerate(siljuk_list):
            # print(data, end='|')
            data_l = data_l+ '|' + data
                
        f.write(data_l+'\n')
        

print('siljuk file save complete ==> {}'.format(file_siljuk_nm))     

0 098120 마이크로컨텍솔
1 131100 스카이이앤엠
2 009520 포스코엠텍
3 095570 AJ네트웍스
4 006840 AK홀딩스
5 282330 BGF리테일
6 027410 BGF
7 138930 BNK금융지주
8 001465 BYC우
9 001460 BYC
10 001045 CJ우
11 00104K CJ4우(전환)
12 001040 CJ
13 011155 CJ씨푸드1우
14 011150 CJ씨푸드
15 058820 CMG제약
16 000590 CS홀딩스
17 012030 DB
18 016610 DB금융투자
19 005830 DB손해보험
20 000995 DB하이텍1우
21 000990 DB하이텍
22 139130 DGB금융지주
23 001530 DI동일
24 000215 DL우
25 001880 DL건설
26 000210 DL
27 37550K DL이앤씨우
28 375500 DL이앤씨
29 155660 DSR
30 069730 DSR제강
31 017940 E1
32 365550 ESR켄달스퀘어리츠
33 050120 ES큐브
34 383220 F&F
35 007700 F&F홀딩스
36 078935 GS우
37 006360 GS건설
38 078930 GS
39 012630 HDC
40 294870 HDC현대산업개발
41 097230 HJ중공업
42 003560 IHQ
43 175330 JB금융지주
44 234080 JW생명과학
45 001065 JW중외제약우
46 001067 JW중외제약2우B
47 001060 JW중외제약
48 096760 JW홀딩스
49 105560 KB금융
50 024120 KB오토시스
51 009070 KCTC
52 044180 KD
53 016385 KG동부제철우
54 016380 KG동부제철
55 001390 KG케미칼
56 033180 KH 필룩스
57 001940 KISCO홀딩스
58 025000 KPX케미칼
59 092230 KPX홀딩스
60 000040 KR모터스
61 093050 LF
62 003555 LG우
63

499 33626K 두산퓨얼셀1우
500 33626L 두산퓨얼셀2우B
501 336260 두산퓨얼셀
502 016740 두올
503 073190 듀오백
504 176750 듀켐바이오
505 030350 드래곤플라이
506 203650 드림시큐리티
507 223250 드림씨아이에스
508 060570 드림어스컴퍼니
509 192650 드림텍
510 217620 디딤
511 187870 디바이스이엔지
512 404950 DB금융스팩10호
513 367340 DB금융스팩8호
514 367360 DB금융스팩9호
515 066670 디스플레이텍
516 024090 디씨엠
517 003160 디아이
518 092200 디아이씨
519 110990 디아이티
520 078590 디아크
521 004840 DRB동일
522 263690 디알젬
523 214680 디알텍
524 377190 디앤디플랫폼리츠
525 263720 디앤씨미디어
526 376300 디어유
527 241520 DSC인베스트먼트
528 109740 디에스케이
529 131030 디에이치피코리아
530 196490 디에이테크놀로지
531 066900 디에이피
532 180400 디엑스앤브이엑스
533 127120 디엔에이링크
534 092070 디엔에프
535 068790 DMS
536 039840 디오
537 219550 디와이디
538 013570 디와이
539 310870 디와이씨
540 210540 디와이파워
541 104460 디와이피엔에프
542 079810 디이엔티
543 113810 디젠스
544 043360 디지아이
545 197140 디지캡
546 068930 디지털대성
547 033130 디지틀조선
548 105740 디케이락
549 263020 디케이앤디
550 290550 디케이티
551 007340 디티알오토모티브
552 187220 디티앤씨
553 163430 디피코
554 131180 딜리
555 315640 딥노이드
556 317120 라닉스
557 042510 라온시큐어
55

992 308170 센트랄모텍
993 012600 센트럴인사이트
994 331920 셀레믹스
995 049180 셀루메드
996 299660 셀리드
997 268600 셀리버리
998 108860 셀바스AI
999 208370 셀바스헬스케어
1000 258250 셀젠텍
1001 068270 셀트리온
1002 068760 셀트리온제약
1003 091990 셀트리온헬스케어
1004 290690 소룩스
1005 053110 소리바다
1006 950200 소마젠
1007 032680 소프트센
1008 032685 소프트센우
1009 258790 소프트캠프
1010 066910 손오공
1011 043100 솔고바이오
1012 33637K 솔루스첨단소재1우
1013 33637L 솔루스첨단소재2우B
1014 336370 솔루스첨단소재
1015 154040 솔루에타
1016 248070 솔루엠
1017 035610 솔본
1018 357780 솔브레인
1019 036830 솔브레인홀딩스
1020 304100 솔트룩스
1021 004430 송원산업
1022 086980 쇼박스
1023 050960 수산아이앤티
1024 017550 수산중공업
1025 084180 수성이노베이션
1026 253840 수젠텍
1027 236200 슈프리마
1028 317770 슈프리마아이디
1029 094840 슈프리마에이치큐
1030 192440 슈피겐코리아
1031 099440 스맥
1032 033790 스카이문스테크놀로지
1033 276040 스코넥
1034 159910 스킨앤스킨
1035 115570 스타플렉스
1036 258540 스템랩
1037 330730 스톤브릿지벤처스
1038 204630 스튜디오산타클로스
1039 253450 스튜디오드래곤
1040 026890 스틱인베스트먼트
1041 013810 스페코
1042 039670 스포츠서울
1043 049830 승일
1044 020710 시공테크
1045 033170 시그네틱스
1046 260870 시그넷이브이
1047 048870 시

1443 093510 엔지브이아이
1444 208860 엔지스테크널러지
1445 183490 엔지켐생명과학
1446 085310 엔케이
1447 182400 엔케이맥스
1448 348370 엔켐
1449 069410 엔텔스
1450 227950 엔투텍
1451 291230 엔피
1452 198080 엔피디
1453 048830 엔피케이
1454 096870 엘디티
1455 276240 엘리비젼
1456 900140 엘브이엠씨홀딩스
1457 376190 엘비루셈
1458 061970 엘비세미콘
1459 138690 엘아이에스
1460 290650 엘앤씨바이오
1461 066970 엘앤에프
1462 156100 엘앤케이바이오
1463 229640 LS전선아시아
1464 311060 엘에이티
1465 108320 LX세미콘
1466 108675 LX하우시스우
1467 108670 LX하우시스
1468 38380K LX홀딩스1우
1469 383800 LX홀딩스
1470 073110 엘엠에스
1471 083310 엘오티베큠
1472 037560 LG헬로비전
1473 037950 엘컴텍
1474 170920 엘티씨
1475 058630 엠게임
1476 058970 엠로
1477 019590 엠벤처투자
1478 097520 엠씨넥스
1479 179290 엠아이텍
1480 225860 엠앤씨생명과학
1481 009780 엠에스씨
1482 123040 엠에스오토텍
1483 323230 엠에프엠코리아
1484 033160 엠케이전자
1485 347890 엠투아이
1486 033310 엠투엔
1487 259630 엠플러스
1488 065150 엠피대산
1489 115960 연우
1490 090740 연이비앤티
1491 060850 영림원소프트랩
1492 014440 영보화학
1493 007530 영신금속
1494 143540 영우디에스피
1495 111770 영원무역
1496 009970 영원무역홀딩스
1497 003520 영진약품
1498 000670 영풍
1499 036560

1911 187420 제노포커스
1912 189350 코셋
1913 023450 동남합성
1914 002380 KCC
1915 044380 주연테크
1916 239340 줌인터넷
1917 024110 기업은행
1918 051980 중앙디앤엠
1919 072020 중앙백신
1920 000440 중앙에너비스
1921 078650 지나인제약
1922 228760 지노믹트리
1923 314130 지놈앤컴퍼니
1924 013890 지누스
1925 389030 지니너스
1926 043610 지니뮤직
1927 263860 지니언스
1928 303030 지니틱스
1929 036180 지더블유바이텍
1930 208350 지란지교시큐리티
1931 144510 지씨셀
1932 382480 지아이텍
1933 382800 지앤비에스엔지니어링
1934 299480 지앤이헬스케어
1935 051160 지어소프트
1936 001250 GS글로벌
1937 007070 GS리테일
1938 053050 지에스이
1939 130500 GH신소재
1940 119850 지엔씨에너지
1941 270520 지엔원에너지
1942 065060 지엔코
1943 204840 지엘팜텍
1944 013870 지엠비코리아
1945 071320 지역난방공사
1946 135160 지오씨
1947 311320 지오엘리먼트
1948 010580 지코
1949 035000 지투알
1950 219750 지티지웰니스
1951 088790 진도
1952 018120 진로발효
1953 109820 진매트릭스
1954 086060 진바이오텍
1955 036890 진성티이씨
1956 363250 진시스템
1957 003780 진양산업
1958 007370 진양제약
1959 010640 진양폴리
1960 100250 진양홀딩스
1961 051630 진양화학
1962 272450 진에어
1963 011000 진원생명과학
1964 250030 진코스텍
1965 002785 진흥기업우B
1966 002787 진흥기업2우B
1967 00278

2372 000087 하이트진로2우B
2373 000080 하이트진로
2374 000145 하이트진로홀딩스우
2375 000140 하이트진로홀딩스
2376 373200 하인크코리아
2377 066130 하츠
2378 004590 한국가구
2379 036460 한국가스공사
2380 039340 한국경제TV
2381 005430 한국공항
2382 034950 한국기업평가
2383 010040 한국내화
2384 025540 한국단자
2385 222980 한국맥널티
2386 331660 한국미라클피플사
2387 318000 한국바이오젠
2388 096300 베트남개발1
2389 256840 한국비엔씨
2390 004090 한국석유
2391 025550 한국선재
2392 002200 한국수출포장
2393 002960 한국쉘석유
2394 017890 한국알콜
2395 000240 한국앤컴퍼니
2396 033270 유나이티드제약
2397 080720 한국유니온제약
2398 123890 한국자산신탁
2399 015760 한국전력
2400 052690 한전기술
2401 063570 한국전자금융
2402 041460 한국전자인증
2403 006200 한국전자홀딩스
2404 101680 한국정밀기계
2405 039740 한국정보공학
2406 053300 한국정보인증
2407 025770 한국정보통신
2408 409570 한국제10호스팩
2409 009540 한국조선해양
2410 023350 한국종합기술
2411 025890 한국주강
2412 000970 한국주철관
2413 104700 한국철강
2414 017960 한국카본
2415 023760 한국캐피탈
2416 054040 한국컴퓨터
2417 050540 한국코퍼레이션
2418 161890 한국콜마
2419 024720 한국콜마홀딩스
2420 021650 한국큐빅
2421 161390 한국타이어앤테크놀로지
2422 053590 한국테크놀로지
2423 034830 한국토지신탁
2424 152550 한국ANKOR유전
2425 16

In [58]:
# 전종목기본정보_20220320.xlsx
file_nm_1 = '전종목기본정보_'+dt_str+'.xlsx'
df1 = pd.read_excel(folder_nm+'/'+ file_nm_1, index_col= 0, dtype={'단축코드':str})
# 칼럼변경 (단축코드->종목코드)
df1.rename(columns={"단축코드":"종목코드"}, inplace=True)
# 칼럼삭제 (표준코드)
df1.drop(['표준코드','한글 종목명','영문 종목명','상장일'], axis='columns', inplace=True) # 칼럼단위 삭제
# for column_name, item in df1.iteritems():
for index, row in df1.iterrows():
    code = row[0]
    code_nm = row[1]
    print(row[0] , row[1])
    

098120 마이크로컨텍솔
131100 스카이이앤엠
009520 포스코엠텍
095570 AJ네트웍스
006840 AK홀딩스
282330 BGF리테일
027410 BGF
138930 BNK금융지주
001465 BYC우
001460 BYC
001045 CJ우
00104K CJ4우(전환)
001040 CJ
011155 CJ씨푸드1우
011150 CJ씨푸드
058820 CMG제약
000590 CS홀딩스
012030 DB
016610 DB금융투자
005830 DB손해보험
000995 DB하이텍1우
000990 DB하이텍
139130 DGB금융지주
001530 DI동일
000215 DL우
001880 DL건설
000210 DL
37550K DL이앤씨우
375500 DL이앤씨
155660 DSR
069730 DSR제강
017940 E1
365550 ESR켄달스퀘어리츠
050120 ES큐브
383220 F&F
007700 F&F홀딩스
078935 GS우
006360 GS건설
078930 GS
012630 HDC
294870 HDC현대산업개발
097230 HJ중공업
003560 IHQ
175330 JB금융지주
234080 JW생명과학
001065 JW중외제약우
001067 JW중외제약2우B
001060 JW중외제약
096760 JW홀딩스
105560 KB금융
024120 KB오토시스
009070 KCTC
044180 KD
016385 KG동부제철우
016380 KG동부제철
001390 KG케미칼
033180 KH 필룩스
001940 KISCO홀딩스
025000 KPX케미칼
092230 KPX홀딩스
000040 KR모터스
093050 LF
003555 LG우
034220 LG디스플레이
003550 LG
051905 LG생활건강우
051900 LG생활건강
373220 LG에너지솔루션
032640 LG유플러스
011070 LG이노텍
066575 LG전자우
066570 LG전자
051915 LG화학우
051910 LG화학
079550 LIG넥스원
010120 LS ELECTRIC
0

031440 신세계푸드
006880 신송홀딩스
002800 신신제약
005800 신영와코루
001725 신영증권우
001720 신영증권
323280 신영스팩5호
344050 신영스팩6호
009275 신원우
009270 신원
017000 신원종합개발
002700 신일전자
012790 신일제약
138070 신진에스엠
226330 신테카바이오
019175 신풍제약우
019170 신풍제약
002870 신풍제지
055550 신한지주
404990 신한서부티엔디리츠
293940 신한알파리츠
333050 신한제6호스팩
366330 신한제7호스팩
393360 신한제8호스팩
056700 신화인터텍
187270 신화콘텍
004080 신흥
243840 신흥에스이씨
257720 실리콘투
222800 심텍
036710 심텍홀딩스
160980 싸이맥스
356890 싸이버원
217330 싸이토젠
102280 쌍방울
003410 쌍용C&E
003620 쌍용차
010280 쌍용정보통신
004770 써니전자
217320 썬테크
208640 썸에이지
222420 쎄노텍
037760 쎄니트
099320 쎄트렉아이
015540 쎌마테라퓨틱스
049960 쎌바이오텍
050890 쏠리드
013720 CBI
066790 씨씨에스
222080 씨아이에스
004920 씨아이테크
236030 씨알푸드
103660 씨앗
352480 씨앤씨인터내셔널
245450 씨앤에스링크
023460 CNH
264660 씨앤지하이테크
352700 씨앤투스성진
056730 CNT85
065770 CS
297090 씨에스베어링
083660 CSA 코스믹
112610 씨에스윈드
359090 씨엔알리서치
286000 씨엔티드림
115530 씨엔플러스
056000 COWON
115480 씨유메디칼
376290 씨유테크
189330 씨이랩
000120 CJ대한통운
311690 CJ 바이오사이언스
079160 CJ CGV
035760 CJ ENM
097955 CJ제일제당 우
097950 CJ제일제당
051500 CJ프레시웨이
096530 

078940 코드네이처
080530 코디
224060 코디엠
357120 코람코에너지리츠
104540 코렌텍
027050 코리아나
290510 코리아센터
007815 코리아써우
00781K 코리아써키트2우B
007810 코리아써키트
190650 코리아에셋투자증권
101670 코리아에스이
123410 코리아에프티
003690 코리안리
036690 코맥스
049430 코메론
183300 코미코
041960 코미팜
089890 코세스
009730 코센
082660 코스나인
192820 코스맥스
044820 코스맥스비티아이
222040 코스맥스엔비티
241710 코스메카코리아
005070 코스모신소재
005420 코스모화학
069110 코스온
169670 코스텍시스템
071950 코아스
166480 코아스템
045970 코아시아
196450 코아시아옵틱스
029960 코엔텍
002025 코오롱우
003075 코오롱글로벌우
003070 코오롱글로벌
002020 코오롱
102940 코오롱생명과학
120115 코오롱인더우
120110 코오롱인더
950160 코오롱티슈진
138490 코오롱플라스틱
021240 코웨이
033290 코웰패션
056360 코위버
282880 코윈테크
121850 코이즈
015710 코콤
052330 코텍
322780 코퍼스코리아
126600 코프라
200130 콜마비앤에이치
031820 콤텍시스템
294570 쿠콘
192400 쿠쿠홀딩스
284740 쿠쿠홈시스
317690 퀀타매트릭스
365270 큐라클
060280 큐렉소
015590 큐로
040350 큐로컴
051780 큐로홀딩스
115180 큐리언트
182360 큐브엔터
066310 큐에스아이
136660 큐엠씨
016600 큐캐피탈
26490K 크라운제과우
264900 크라운제과
005745 크라운해태홀딩스우
005740 크라운해태홀딩스
259960 크래프톤
096240 크레버스
215570 크로넥스
043590 크로바하이텍
114120 크루셜텍
110790 크리스에프앤씨
083790 크리

In [62]:
global aaa_lists
aaa_lists = []

file_siljuk_nm = '실적_'+dt_str+'.csv'

file_nm = 'test.csv'

int_index_1 = 'N'
idx = 0
with open(folder_nm+'/'+ file_siljuk_nm,'r') as f:
    for line in f:
        if (line.find('주요재무정보') > 0 and int_index_1 == 'Y'):
            int_index_1 = 'Y'
            continue;
        if line.find('PER') > 0:
            continue;
        if line.find('시가총액') > 0:
            continue;
        line = line.replace('|',',')
        aaa_lists.append(line.replace('|',','))
        idx = idx +1
        print(idx, line)
 


1 ,종목코드,종목한글명,주요재무정보,2019.12,2020.12,2021.12,2022.12(E),2020.12,2021.03,2021.06,2021.09,2021.12,2022.03(E)

2 ,098120,마이크로컨텍솔,매출액,344,393,614,,112,109,147,167,190,

3 ,098120,마이크로컨텍솔,영업이익,6,17,79,,2,13,14,36,16,

4 ,098120,마이크로컨텍솔,당기순이익,8,11,76,,-1,18,6,38,14,

5 ,098120,마이크로컨텍솔,영업이익률,1.80,4.21,12.93,,1.93,12.14,9.68,21.56,8.28,

6 ,098120,마이크로컨텍솔,순이익률,2.41,2.85,12.34,,-1.03,16.42,4.07,22.52,7.42,

7 ,098120,마이크로컨텍솔,ROE(지배주주),2.77,3.32,19.78,,3.32,10.15,9.13,16.09,19.78,

8 ,098120,마이크로컨텍솔,부채비율,14.00,23.88,23.29,,23.88,16.65,23.98,22.78,23.29,

9 ,098120,마이크로컨텍솔,당좌비율,465.35,315.16,322.39,,315.16,443.58,319.48,346.41,322.39,

10 ,098120,마이크로컨텍솔,유보율,696.42,723.80,899.52,,723.80,761.66,775.87,866.07,899.52,

11 ,098120,마이크로컨텍솔,EPS(원),108,135,904,,-14,214,71,451,168,

12 ,098120,마이크로컨텍솔,BPS(원),3,983,4,134,5,012,,4,134,4,324,4,394,4,845,5,012,

13 ,098120,마이크로컨텍솔,PBR(배),1.22,1.49,2.81,,1.49,1.33,1.77,1.67,2.81,

14 ,098120,마이크로컨텍솔,주당배당금(원),-,25,30,,,,,,,

15 ,098120,마이크로컨텍솔,시가배당률(%),-,0.41,

1266 ,035420,NAVER,매출액,43,562,53,041,68,176,83,755,15,126,14,991,16,635,17,273,19,277,18,939

1267 ,035420,NAVER,영업이익,11,550,12,153,13,255,16,190,3,238,2,888,3,356,3,498,3,512,3,582

1268 ,035420,NAVER,당기순이익,3,968,8,450,164,776,16,921,3,841,153,145,5,406,3,227,2,998,3,761

1269 ,035420,NAVER,영업이익률,26.51,22.91,19.44,19.33,21.40,19.27,20.18,20.25,18.22,18.92

1270 ,035420,NAVER,순이익률,9.11,15.93,241.69,20.20,25.39,1,021.60,32.49,18.68,15.55,19.86

1271 ,035420,NAVER,ROE(지배주주),10.56,15.21,106.72,7.00,15.21,112.29,111.05,109.92,106.72,

1272 ,035420,NAVER,부채비율,89.11,106.11,40.22,,106.11,35.65,36.24,36.17,40.22,

1273 ,035420,NAVER,당좌비율,146.37,37.38,128.35,,37.38,119.58,109.19,97.68,128.35,

1274 ,035420,NAVER,유보율,44,216.06,51,258.50,149,081.45,,51,258.50,140,890.23,144,908.70,147,527.84,149,081.45,

1275 ,035420,NAVER,EPS(원),3,538,6,097,100,400,10,410,2,585,93,207,3,212,2,021,1,948,2,328

1276 ,035420,NAVER,BPS(원),39,913,49,961,157,753,169,321,49,961,148,906,153,343,159,091,157,753,

1277 ,0

2516 ,038530,골드퍼시픽,당기순이익,-50,-316,-15,,39,97,-72,20,-53,

2517 ,038530,골드퍼시픽,영업이익률,-14.04,-30.21,4.78,,-2.18,22.57,-6.94,-18.38,-169.63,

2518 ,038530,골드퍼시픽,순이익률,-62.40,-279.11,-10.45,,122.73,233.88,-197.61,59.98,-611.00,

2519 ,038530,골드퍼시픽,ROE(지배주주),,-153.58,-3.71,,-94.95,-3.71,-1.93,18.28,-1.74,

2520 ,038530,골드퍼시픽,부채비율,87.68,246.22,19.56,,107.55,19.56,29.67,24.04,19.09,

2521 ,038530,골드퍼시픽,당좌비율,157.24,48.54,225.74,,69.67,225.74,241.49,279.35,356.04,

2522 ,038530,골드퍼시픽,유보율,138.56,25.44,80.91,,26.60,80.91,67.90,80.78,71.52,

2523 ,038530,골드퍼시픽,EPS(원),-389,-1,097,-33,,85,158,-105,26,-67,

2524 ,038530,골드퍼시픽,BPS(원),1,184,623,903,,631,903,838,903,856,

2525 ,038530,골드퍼시픽,PBR(배),1.20,2.60,1.59,,2.38,1.59,1.52,1.53,2.44,

2526 ,038530,골드퍼시픽,주당배당금(원),,-,,,,,,,,

2527 ,038530,골드퍼시픽,시가배당률(%),,-,,,,,,,,

2528 ,038530,골드퍼시픽,배당성향(%),-,,-,,,,,,,

2529 ,종목코드,종목한글명,주요재무정보,2019.12,2020.12,2021.12,2022.12(E),2020.12,2021.03,2021.06,2021.09,2021.12,2022.03(E)

2530 ,215000,골프존,매출액,2,470,2,985,4,403,

3766 ,004270,남성,순이익률,-4.30,-3.01,-17.48,,1.66,-55.28,7.76,5.50,2.92,

3767 ,004270,남성,ROE(지배주주),-4.11,-2.52,-19.75,,-5.06,-19.75,-16.68,-14.47,-14.35,

3768 ,004270,남성,부채비율,147.78,138.34,156.07,,158.96,156.07,162.39,156.57,198.41,

3769 ,004270,남성,당좌비율,47.75,54.94,58.30,,55.17,58.30,59.34,73.70,67.55,

3770 ,004270,남성,유보율,385.27,396.95,322.37,,390.35,322.37,328.94,336.34,339.35,

3771 ,004270,남성,EPS(원),-97,-59,-442,,12,-420,50,37,15,

3772 ,004270,남성,BPS(원),3,055,2,842,2,422,,2,794,2,422,2,413,2,459,2,420,

3773 ,004270,남성,PBR(배),0.63,1.11,1.74,,1.01,1.74,1.65,1.59,1.45,

3774 ,004270,남성,주당배당금(원),25,25,35,,,,,,,

3775 ,004270,남성,시가배당률(%),1.31,0.79,0.83,,,,,,,

3776 ,004270,남성,배당성향(%),-8.98,-19.32,-3.94,,,,,,,

3777 ,종목코드,종목한글명,주요재무정보,2018.12,2019.12,2020.12,2021.12(E),2020.09,2020.12,2021.03,2021.06,2021.09,2021.12(E)

3778 ,003925,남양유업우,매출액,10,797,10,308,9,489,,2,459,2,274,2,309,2,396,2,401,

3779 ,003925,남양유업우,영업이익,86,4,-771,,-146,-300,-138,-212,-230,

3780 ,003925,남양유업우,당기순이익,20,292


5266 ,290670,대보마그네틱,매출액,206,239,158,380,30,30,63,79,110,129

5267 ,290670,대보마그네틱,영업이익,42,47,-12,55,-6,-10,4,17,15,19

5268 ,290670,대보마그네틱,당기순이익,34,38,-12,45,-8,-11,5,13,12,16

5269 ,290670,대보마그네틱,영업이익률,20.38,19.49,-7.91,14.47,-20.71,-34.56,6.47,21.73,13.28,14.73

5270 ,290670,대보마그네틱,순이익률,16.51,16.02,-7.36,11.84,-27.19,-37.60,8.03,16.00,10.87,12.40

5271 ,290670,대보마그네틱,ROE(지배주주),18.44,11.79,-2.95,9.80,0.27,-2.95,-1.69,-0.39,3.77,

5272 ,290670,대보마그네틱,부채비율,24.79,76.97,48.23,,66.40,48.23,34.03,34.80,19.44,

5273 ,290670,대보마그네틱,당좌비율,388.95,1,053.45,181.65,,159.64,181.65,205.40,177.14,277.91,

5274 ,290670,대보마그네틱,유보율,1,641.85,950.27,1,163.83,,1,099.15,1,163.83,1,311.29,1,356.72,1,525.46,

5275 ,290670,대보마그네틱,EPS(원),628,593,-173,591,-121,-160,69,169,153,204

5276 ,290670,대보마그네틱,BPS(원),4,604,5,497,6,326,6,461,5,957,6,326,7,096,7,097,7,742,6,461

5277 ,290670,대보마그네틱,PBR(배),7.73,4.08,5.68,9.01,5.82,5.68,4.52,4.83,4.13,9.01

5278 ,290670,대보마그네틱,주당배당금(원),,,-,-,,,,,,

5279 ,290670,대보마그네틱,시가배당률(%)

...

33011 ,033830,티비씨,영업이익,52,29,43,,30,3,13,18,9,

33012 ,033830,티비씨,당기순이익,56,38,46,,26,5,14,18,10,

33013 ,033830,티비씨,영업이익률,10.65,8.26,10.11,,24.86,3.93,13.06,18.83,5.93,

33014 ,033830,티비씨,순이익률,11.30,10.68,10.80,,21.98,6.82,13.51,19.09,6.00,

33015 ,033830,티비씨,ROE(지배주주),5.13,3.36,4.02,,3.36,4.17,4.20,5.58,4.02,

33016 ,033830,티비씨,부채비율,9.99,5.57,8.28,,5.57,5.72,5.85,6.22,8.28,

33017 ,033830,티비씨,당좌비율,274.60,483.89,298.08,,483.89,931.05,413.11,926.33,298.08,

33018 ,033830,티비씨,유보율,129.40,134.39,141.57,,134.39,133.52,136.25,139.86,141.57,

33019 ,033830,티비씨,EPS(원),56,38,46,,26,5,14,18,10,

33020 ,033830,티비씨,BPS(원),1,171,1,199,1,240,,1,199,1,195,1,211,1,232,1,240,

33021 ,033830,티비씨,PBR(배),1.03,0.91,1.13,,0.91,1.21,1.30,1.79,1.13,

33022 ,033830,티비씨,주당배당금(원),16,10,13,,,,,,,

33023 ,033830,티비씨,시가배당률(%),1.32,0.92,0.93,,,,,,,

33024 ,033830,티비씨,배당성향(%),27.17,25.09,26.55,,,,,,,

33025 ,종목코드,종목한글명,주요재무정보,2018.12,2019.12,2020.12,2021.12(E),2020.09,2020.12,2021.03,2021.06,2021.09,2021.12(E)

33026


34511 ,203690,프로스테믹스,시가배당률(%),,-,-,,,,,,,

34512 ,203690,프로스테믹스,배당성향(%),-,-,-,,,,,,,

34513 ,종목코드,종목한글명,주요재무정보,2018.12,2019.12,2020.12,2021.12(E),2020.09,2020.12,2021.03,2021.06,2021.09,2021.12(E)

34514 ,321260,프로이천,매출액,235,297,288,,-,-,-,-,,

34515 ,321260,프로이천,영업이익,17,30,27,,-,-,-,-,-1,

34516 ,321260,프로이천,당기순이익,15,23,21,,-,-,-,-,-1,

34517 ,321260,프로이천,영업이익률,7.23,10.01,9.21,,,,,,,

34518 ,321260,프로이천,순이익률,6.23,7.60,7.20,,,,,,,

34519 ,321260,프로이천,ROE(지배주주),23.53,27.95,,,0.45,0.33,0.14,-0.02,,

34520 ,321260,프로이천,부채비율,97.52,115.68,36.69,,17.14,16.95,17.08,17.23,17.29,

34521 ,321260,프로이천,당좌비율,198.29,191.62,407.56,,,,,,,

34522 ,321260,프로이천,유보율,1,536.28,2,067.98,3,548.37,,1,846.85,1,848.91,1,845.50,1,844.89,1,828.35,

34523 ,321260,프로이천,EPS(원),56,87,80,,,2,,,-2,

34524 ,321260,프로이천,BPS(원),268,355,582,,,1,949,,,250,

34525 ,321260,프로이천,PBR(배),,,,,1.03,1.06,1.09,1.19,13.09,

34526 ,321260,프로이천,주당배당금(원),,,,,,,,,,

34527 ,321260,프로이천,시가배당률(%),,,,,,,,,,

34528 ,321260,프로이천,배당성향(%),-,-,-,

36010 ,039740,한국정보공학,유보율,902.01,939.39,836.85,,873.49,836.85,828.37,872.31,895.41,

36011 ,039740,한국정보공학,EPS(원),-1,080,223,-487,,-24,-159,-44,220,114,

36012 ,039740,한국정보공학,BPS(원),4,836,5,025,4,544,,4,700,4,544,4,499,4,719,4,833,

36013 ,039740,한국정보공학,PBR(배),0.67,0.61,0.81,,0.64,0.81,0.75,1.16,1.18,

36014 ,039740,한국정보공학,주당배당금(원),-,-,-,,,,,,,

36015 ,039740,한국정보공학,시가배당률(%),-,-,-,,,,,,,

36016 ,039740,한국정보공학,배당성향(%),,-,-,,,,,,,

36017 ,종목코드,종목한글명,주요재무정보,2019.12,2020.12,2021.12,2022.12(E),2020.12,2021.03,2021.06,2021.09,2021.12,2022.03(E)

36018 ,053300,한국정보인증,매출액,426,457,589,,118,129,125,128,206,

36019 ,053300,한국정보인증,영업이익,93,104,117,,22,34,30,25,28,

36020 ,053300,한국정보인증,당기순이익,71,98,126,,29,50,24,24,28,

36021 ,053300,한국정보인증,영업이익률,21.76,22.80,19.82,,18.48,26.46,24.03,19.26,13.47,

36022 ,053300,한국정보인증,순이익률,16.76,21.34,21.32,,24.57,38.45,19.22,18.35,13.69,

36023 ,053300,한국정보인증,ROE(지배주주),8.65,11.09,9.69,,11.09,15.62,13.73,9.72,9.69,

36024 ,053300,한국정보인증,부채비율,28.12,30.94,27.86,,30.94,33

37510 ,009835,한화솔루션우,순이익률,-2.63,3.28,5.75,4.68,-3.88,16.02,8.02,7.50,-6.25,3.67

37511 ,009835,한화솔루션우,ROE(지배주주),-4.02,5.30,8.79,7.05,5.30,9.36,10.07,9.90,8.79,

37512 ,009835,한화솔루션우,부채비율,170.09,153.65,143.96,,153.65,119.06,113.35,114.02,143.96,

37513 ,009835,한화솔루션우,당좌비율,60.12,60.31,64.56,,60.31,92.88,96.22,83.02,64.56,

37514 ,009835,한화솔루션우,유보율,606.50,636.68,721.16,,636.68,695.04,720.57,732.48,721.16,

37515 ,009835,한화솔루션우,EPS(원),-1,403,1,843,3,305,2,932,-564,2,215,1,159,1,007,-957,483

37516 ,009835,한화솔루션우,BPS(원),33,924,35,551,42,563,41,077,35,551,40,237,41,885,43,103,42,563,

37517 ,009835,한화솔루션우,PBR(배),0.54,1.31,0.83,0.85,1.31,1.25,1.06,1.04,0.83,

37518 ,009835,한화솔루션우,주당배당금(원),250,,,208,,,,,,

37519 ,009835,한화솔루션우,시가배당률(%),2.11,,,,,,,,,

37520 ,009835,한화솔루션우,배당성향(%),-13.71,-,,,,,,,,

37521 ,종목코드,종목한글명,주요재무정보,2019.12,2020.12,2021.12,2022.12(E),2020.12,2021.03,2021.06,2021.09,2021.12,2022.03(E)

37522 ,009830,한화솔루션,매출액,94,574,91,950,107,252,119,889,25,618,24,043,27,775,25,803,29,631

39010 ,353190,휴럼,매출액,667,768,691,,-,-,-,166,138,

39011 ,353190,휴럼,영업이익,51,74,13,,-,-,-,12,-11,

39012 ,353190,휴럼,당기순이익,27,21,-73,,-,-,-,-34,-43,

39013 ,353190,휴럼,영업이익률,7.59,9.70,1.83,,,,,7.18,-8.03,

39014 ,353190,휴럼,순이익률,4.07,2.70,-10.53,,,,,-20.49,-31.15,

39015 ,353190,휴럼,ROE(지배주주),,41.13,-34.80,,,,-0.57,,,

39016 ,353190,휴럼,부채비율,942.06,459.91,32.93,,22.29,22.44,22.56,33.44,32.93,

39017 ,353190,휴럼,당좌비율,57.64,59.16,245.59,,,,,309.95,245.59,

39018 ,353190,휴럼,유보율,75.54,266.17,856.06,,1,769.60,1,767.80,1,760.99,881.40,856.06,

39019 ,353190,휴럼,EPS(원),92,67,-216,,-1,,,-97,-118,

39020 ,353190,휴럼,BPS(원),103,220,956,,1,870,,,981,956,

39021 ,353190,휴럼,PBR(배),,,1.78,,1.12,1.17,1.63,2.05,1.78,

39022 ,353190,휴럼,주당배당금(원),,,,,,,,,,

39023 ,353190,휴럼,시가배당률(%),,,,,,,,,,

39024 ,353190,휴럼,배당성향(%),-,-,,,,,,,,

39025 ,종목코드,종목한글명,주요재무정보,2018.12,2019.12,2020.12,2021.12(E),2020.09,2020.12,2021.03,2021.06,2021.09,2021.12(E)

39026 ,090710,휴림로봇,매출액,307,176,207,,83,23,69,80,72,

39027 ,090710,휴림로봇,영업

In [61]:
df_aaa = pd.read_csv(folder_nm+'/'+ file_siljuk_nm,'r') 
df_aaa.head()

|종목코드|종목한글명|주요재무정보|2019.12|2020.12|2021.12|2022.12(E)|2020.12|2021.03|2021.06|2021.09|2021.12|2022.03(E)
0  |098120|마이크로컨텍솔|매출액|344|393|614||112|109|147|1...                                                      
1       |098120|마이크로컨텍솔|영업이익|6|17|79||2|13|14|36|16|                                                      
2      |098120|마이크로컨텍솔|당기순이익|8|11|76||-1|18|6|38|14|                                                      
3  |098120|마이크로컨텍솔|영업이익률|1.80|4.21|12.93||1.93|12...                                                      
4  |098120|마이크로컨텍솔|순이익률|2.41|2.85|12.34||-1.03|16...